# Explore Cluster Power Stats 

Use rest api for now to avoid RPC issues with python client library.

Convert a curl command for currnet power to rest query
https://curl.trillworks.com/

This is the curl command that confirms authenticated access to Bright's CMDaeamon. It was derived from the [RestAPI intro in the Bright Developer Manual](https://support.brightcomputing.com/manuals/8.2/developer-manual.pdf).

```
curl --cert ~/.cm/cert.pem --key ~/.cm/cert.key --cacert pythoncm/etc/cacert.pem \
     "https://master:8081/rest/v1/monitoring/latest?measurable=Pwr_Consumption&indent=1"
```

Getting the total instantaneous power used from all nodes monitored by cmd.  The sum on the deals with weird outlier data from one of the nods:

```
curl --cert ~/.cm/cert.pem --key ~/.cm/cert.key --cacert pythoncm/etc/cacert.pem \
     "https://master:8081/rest/v1/monitoring/latest?measurable=Pwr_Consumption&indent=1" | \
     jq '.data[] | select(.raw < 10000) .raw' | \
     awk '{sum=$1+sum} END {print sum}'
```

In [ ]:
import requests
import pprint
import datetime
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import matplotlib.dates as mdates

In [ ]:
pp = pprint.PrettyPrinter(indent=2)

Set up credentials to query RestAPI. Bright controls access based on the user identity.  The user's cert.pem and cert.key are automatically generated but the cacert.pem needs to be constructed from the  certs returned by the master.

In [ ]:
cert_file='/home/jpr/.cm/cert.pem'
key_file='/home/jpr/.cm/cert.key'
ca_file='/home/jpr/projects/power-study/pythoncm/etc/cacert.pem'

In [ ]:
params = (
    ('measurable', 'Pwr_Consumption'),
    ('indent', '1'),
)

In [ ]:
cert=(cert_file, key_file)

In [ ]:
# define the client certs with the cert line, note the order is (cert, key)
# https://requests.readthedocs.io/en/master/user/advanced/#client-side-certificates
#
# define the verify bundle via verify, note False means do not verify
# https://stackoverflow.com/a/48636689/8928529
response = requests.get('https://master:8081/rest/v1/monitoring/latest', params=params, cert=cert, verify=False)

Manually construct a pthyon datastructure hash of nodes and tuples of power sample.

In [ ]:
debug=False
power=0.0
count=0
for num, doc in enumerate(response.json()["data"]):
    if doc["age"] < 1000:
       if debug: print("{}: {}\n".format(num, pp.pprint(doc)))
       if doc["value"] != "no data":
         power=power + float(doc["raw"])
         count+=1

In [ ]:
power

In [ ]:
power/count

In [ ]:
count

Note that the time is in milleseconds so the unix converstion needs to drop the last three digits.

## Get power use history

From beginning of july for starters. Based on the blog https://www.dataquest.io/blog/tutorial-time-series-analysis-with-pandas/.

In [ ]:
params = (
    ('start', '2020/01/01 00:00'),
    #('entity', 'c0109'),
    ('measurable', 'Pwr_Consumption'),
    ('indent', '1'),
)

In [ ]:
response = requests.get('https://master:8081/rest/v1/monitoring/dump', params=params, cert=cert, verify=False)

response.json()

It's easy to [convert a list of dictionaries to a pandas data frame](https://pbpython.com/pandas-list-dict.html). This conversion path is the default for the pandas DataFrame constructor and serves our currnt needs well. We can create data frame from the power dump response and easily enhance the data to serve our plotting needs.

In [ ]:
df = pd.DataFrame(response.json()["data"])

In [ ]:
df

In [ ]:
df 

convert result date to unix time stamp for easier plotting and time comparison.

```entity 	measurable 	raw 	time 	value 	datetime 	utime
428473 	c0063 	Pwr_Consumption 	742849.191667 	2020/05/17 23:22:00 	742KW 	2020-05-17 23:22:00 	1589757720

```

In [ ]:
# remove problematic entries, like unrealistic data points.  Nodes can't consume 100's kW, like c0063 on 2020/05/17
# https://www.interviewqs.com/ddi_code_snippets/rows_cols_python
df.loc[df['raw'] >  100000]

In [ ]:
df = df.loc[df['raw'] <  100000]

In [ ]:
# improve performace by providing format string to avoid per-entry parsing deduction

df['datetime'] = pd.to_datetime(df.time, format="%Y/%m/%d %H:%M:%S")

In [ ]:
df

### Initial Data Viz with Seaborn Plots

In [ ]:
# add column with datetime converted to unix time (in seconds) 
# to preserve spacial relationships on the axis
# note: the original data has no time zone so our reference time stamp needs to be timezone free
df['utime'] = (df['datetime'] - pd.Timestamp("1970-01-01T00:00:00.000")) // pd.Timedelta('1s') 

Our default utility function to fix labels on the x-axis of time series seaborn plots

In [ ]:
def timeticks(ax, tformat="%H:%M:%S\n%Y-%m-%d"):
    xticks = ax.get_xticks()
    xticks_dates = [datetime.datetime.fromtimestamp(x).strftime(tformat) for x in xticks]
    hush = ax.set_xticklabels(xticks_dates)
    

Plot each data point for power used. Observe that this plot does not aggregate power use across nodes.  It simply plots power used at all available time plots.

Also note the time outliers.  We requested data since July 1, 2020 but the results include information from 2018.

In [ ]:
# build the replot and capture the handle
g = sns.relplot(x="utime", y="raw",
            palette="bright",
            #height=5,
            aspect=2,
            data=df,
            s=100)
# update the axis labels
g = (g.set_axis_labels("Date", "Power (Watts)"))
# update the x tickmarks from unix time to hour minute seconds
ax = g.axes
ax = ax[0,0]
timeticks(ax)

## Explore Resampling to Hourly Sample

We are more interested in a plot of total power used over time.

We can [resample a data frame on a time interval](https://stackoverflow.com/a/52057318/8928529), which is our interest at this point.  In particular we would find it interesting to see the hourly total (sum) of the raw power used across the cluster.

In [ ]:
hourly = df.resample('H', on='datetime').size().reset_index(name='sum')


In [ ]:
hourly

In [ ]:
hourly["sum"].plot()

This is isn't quite the sum we wanted to add up.

Understand how setting the datatime index moves it out of the column collection

In [ ]:
df.dtypes

In [ ]:
daily = df.set_index('datetime')

In [ ]:
daily.dtypes

In [ ]:
daily

In [ ]:
daily.index

In [ ]:
daily['hourly'] = daily.index.hour

In [ ]:
daily

The date indexing by setting the datetime index is helpful.

In [ ]:
daily.loc['2020-10-05']

In [ ]:
# Use seaborn style defaults and set the default figure size
sns.set(rc={'figure.figsize':(11, 4)})

In [ ]:
daily['raw'].plot()

In [ ]:
axes = daily['raw'].plot(marker='.', alpha=0.5, linestyle='None', figsize=(11, 4), subplots=True)
for ax in axes:
    ax.set_ylabel('Usage (Watts)')

In [ ]:
daily.loc['2020-9', 'raw'].plot(marker='.', alpha=0.5, linestyle='None')

In [ ]:
daily.loc['2020-10-14', 'raw'].plot(marker='.', alpha=0.5, linestyle='None')

In [ ]:
daily.loc['2020-06-15', 'raw'].plot(marker='.', alpha=0.5, linestyle='None')

In [ ]:
daily.loc['2020-06-16', 'raw'].plot(marker='.', alpha=0.5, linestyle='None')

In [ ]:
hourly = daily['raw'].resample('H').sum()

In [ ]:
hourly

In [ ]:
hourly.plot()

In [ ]:
daily['raw'].resample('H').mean().plot()

These plots are interesting but don't seem to capture the data accurately.

It seems more appopriate to work with each inidividual node and structure its values into a standard bin arrangement.

In [ ]:
df

Explore performance of an individual node.

In [ ]:
node=df[df.entity=='c0149']

In [ ]:
node

In [ ]:
node.dtypes

In [ ]:
node = node.set_index("datetime")

In [ ]:
node.dtypes

In [ ]:
node.index

In [ ]:
node

A series of plots for the single node shows times when the node was computing vs when not. Notice the saw tooth graph after the high load events.

In [ ]:
node['raw'].plot()

In [ ]:
node['raw'].plot(marker='.', alpha=0.5, linestyle='None')

Notice the dip in power use right at the the interesting time point.

In [ ]:
node.loc['2020-01-15':'2021-2-16', 'raw'].plot(marker='o', linestyle='-')

In [ ]:
hourly=pd.date_range('2020-05-01', 'now', freq='H')

In [ ]:
hourly=node[['raw']].resample('H').mean()

In [ ]:
hourly['raw'].plot()

Understand summing over the nodes.

In [ ]:
hourly.index

In [ ]:
hourly

In [ ]:
hourly['raw'].isNull()

In [ ]:
hourly_idx=pd.date_range('2020-05-01', '2020-07-09', freq='H')

In [ ]:
len(hourly_idx)

In [ ]:
np.zeros((1,10)).T

In [ ]:
hourly_pwr=pd.DataFrame(np.zeros((1,len(hourly_idx))).T, index=hourly_idx, columns=['raw'])

In [ ]:
hourly_pwr

In [ ]:
hourly_pwr.dtypes

In [ ]:
hourly_pwr.index

Get first or last entry from index. https://stackoverflow.com/a/31269098/8928529

It was easier to append columns to the data frame than to try an add them in a loop.
Do the addition after the columns are built.

In [ ]:
hourly_pwr=pd.DataFrame(np.zeros((1,len(hourly_idx))).T, index=hourly_idx, columns=['raw'])

for num, entity in enumerate(df.entity.unique()):
    if entity not in ['c0108', 'c0009']:
        node_pwr=df[df.entity==entity].set_index("datetime")
        node_pwr=node_pwr[['raw']].resample('H').mean()
        node_pwr=node_pwr['2020-05-01':'2020-07-09'].fillna(method="ffill")
        print(node_pwr)
        missing = node_pwr['raw'].isnull().sum()
        print("{}: {} missing {}\n".format(num, entity, missing))
        if num < 149:
            #hourly_pwr.add(node_pwr['2020-05-01':'2020-07-09'], ['raw'])#, axis='columns', fill_value=0.0)
            #hourly_pwr+=node_pwr['2020-05-01':'2020-07-09']
            # its easier to add columns and do the sum later
            # https://www.geeksforgeeks.org/adding-new-column-to-existing-dataframe-in-pandas/
            hourly_pwr[entity]= node_pwr['2020-05-01':'2020-07-09']


In [ ]:
hourly_pwr

In [ ]:
hourly_pwr.sum(axis=1)

In [ ]:
hourly_pwr.sum(axis=1).plot()